# KorQuad 데이터셋 OpenAI GPT Fine-Tuning

https://huggingface.co/datasets/KorQuAD/squad_kor_v1


KorQuAD(Korean Question Answering Dataset)는 한국어 자연어 처리(NLP)  
분야에서 기계독해(Machine Reading Comprehension, MRC) 모델의 학습과  
평가를 위해 개발된 대규모 공개 질의응답 데이터셋이다. LG CNS에서  
주도적으로 구축하였으며, 영어의 대표적인 MRC 데이터셋인 SQuAD(Stanford  
Question Answering Dataset)의 구조를 참고하여 한국어에 맞게 설계되었다.

## 데이터 준비

In [1]:
import requests # HTTP 요청으로 파일 다운로드하는 라이브러리

url = 'https://raw.githubusercontent.com/korquad/korquad.github.io/refs/heads/master/dataset/KorQuAD_v1.0_dev.json'
r = requests.get(url)   # URL로 GET 요청 전송(응답에 파일 내용 포함)

with open("korQuAD_v1.0_dev.json", "wb") as f:  # 바이너리 쓰기 모드로 파일 생성/열기
    f.write(r.content)                          # 본문 (파일 바이트 데이터)만 그대로 파일에 작성

In [2]:
import json     # JSON 파일을 파이썬 객체로 변환 모듈

with open("korQuAD_v1.0_dev.json","r", encoding='utf-8') as f:
    json_data = json.load(f)    # JSON 내용을 파이썬 dict/list 구조로 로드
    
json_data

{'version': 'KorQuAD_v1.0_dev',
 'data': [{'paragraphs': [{'qas': [{'answers': [{'text': '1989년 2월 15일',
         'answer_start': 0}],
       'id': '6548850-0-0',
       'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?'},
      {'answers': [{'text': '임수경', 'answer_start': 125}],
       'id': '6548850-0-1',
       'question': '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?'},
      {'answers': [{'text': '1989년', 'answer_start': 0}],
       'id': '6548853-0-0',
       'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?'},
      {'answers': [{'text': '학생회관 건물 계단', 'answer_start': 365}],
       'id': '6548853-0-1',
       'question': '임종석을 검거한 장소는 경희대 내 어디인가?'},
      {'answers': [{'text': '서울지방경찰청 공안분실', 'answer_start': 457}],
       'id': '6548853-0-2',
       'question': '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?'},
      {'answers': [{'text': '임종석', 'answer_start': 87}],
       'id': '6332405-0-0',
       'question': '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?'},
      {'answers': [{'text': '여의도 농민 폭력 시위', 

In [3]:
data = json_data['data']    # 최상위데이터 리스트
print(len(data))            # topic(문서)의 개수

140


In [4]:
# 문서 단위로 순회
for topic in data:
    print(topic)
    paragraphs = topic['paragraphs']    # 문서 내 문단(지문) 리스트
    # print(paragraphs)
    for item in paragraphs:             # 지문(문단 텍스트) 순회
        context = item['context']       # 지문 추출
        print(context)
        qas = item['qas']
        for qa in qas:
            question = qa['question']
            answer = qa['answers'][0]['text']
            print(">", question, "->", answer)

{'paragraphs': [{'qas': [{'answers': [{'text': '1989년 2월 15일', 'answer_start': 0}], 'id': '6548850-0-0', 'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?'}, {'answers': [{'text': '임수경', 'answer_start': 125}], 'id': '6548850-0-1', 'question': '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?'}, {'answers': [{'text': '1989년', 'answer_start': 0}], 'id': '6548853-0-0', 'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?'}, {'answers': [{'text': '학생회관 건물 계단', 'answer_start': 365}], 'id': '6548853-0-1', 'question': '임종석을 검거한 장소는 경희대 내 어디인가?'}, {'answers': [{'text': '서울지방경찰청 공안분실', 'answer_start': 457}], 'id': '6548853-0-2', 'question': '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?'}, {'answers': [{'text': '임종석', 'answer_start': 87}], 'id': '6332405-0-0', 'question': '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?'}, {'answers': [{'text': '여의도 농민 폭력 시위', 'answer_start': 13}], 'id': '6332405-0-1', 'question': '임종석이 1989년 2월 15일에 지명수배 받은 혐의는 어떤 시위를 주도했다는 것인가?'}], 'context': '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의(폭력행위등처벌에관한법률위반)으

In [5]:
# 학습 가능한 형태로 데이터 정제
refined_dict = {}   # 질문 -> 답변을 저장할 딕셔너리

for topic in data:                              # 문서 단위로 순회
    paragraphs = topic['paragraphs']            # 문서 내 문단(지문) 리스트
    for item in paragraphs:                     # 문단 텍스트 단위 순회
        qas = item['qas']                       # 해당 지문에 연결도니 Q&A 목록 추출
        for qa in qas:                          # 질문 리스트 순회
            question = qa['question']           # 질문 텍스트
            answer = qa['answers'][0]['text']   # 첫번쨰 정답 텍스트 추출
            refined_dict[question] = answer     # 질문은 key로, 정답은 value로 저장
            
refined_dict

{'임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?': '1989년 2월 15일',
 '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?': '임수경',
 '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?': '1989년',
 '임종석을 검거한 장소는 경희대 내 어디인가?': '학생회관 건물 계단',
 '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?': '서울지방경찰청 공안분실',
 '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?': '임종석',
 '임종석이 1989년 2월 15일에 지명수배 받은 혐의는 어떤 시위를 주도했다는 것인가?': '여의도 농민 폭력 시위',
 '정부의 헌법개정안 준비 과정에 대해서 청와대 비서실이 아니라 국무회의 중심으로 이뤄졌어야 했다고 지적한 원로 헌법학자는?': '허영',
 "'행보가 비서 본연의 역할을 벗어난다', '장관들과 내각이 소외되고 대통령비서실의 권한이 너무 크다'는 의견이 제기된 대표적인 예는?": '10차 개헌안 발표',
 '국무회의의 심의를 거쳐야 한다는 헌법 제 몇 조의 내용인가?': '제89조',
 '법무부 장관을 제쳐놓고 민정수석이 개정안을 설명하는 게 이해가 안 된다고 지적한 경희대 석좌교수 이름은?': '허영',
 '미국 군대 내 두번째로 높은 직위는 무엇인가?': '미국 육군 부참모 총장',
 '로널드 레이건 정부 출범 당시 알렉산더 헤이그는 어떤 직책을 맡았는가?': '초대 국무장관직',
 '알렉산더 헤이그는 어느 대통령의 밑에서 국무장관을 지냈는가?': '로널드 레이건 대통령',
 '로널드 레이건 대통령 밑에서 일한 국무 장관은 누구인가?': '알렉산더 메이그스 헤이그 2세',
 '미국 군대에서 두번째로 높은 직위는?': '미국 육군 부참모 총장',
 '알렉산더 메이그스 헤이그의 생년월일은?': '1924년 12월 2일',
 '알렉산더 헤이그가 로널드 레이건 대통령 밑에서 맡은 직책은 무엇이었나?': '국무장

In [6]:
print(len(refined_dict))        # refined_dict에 저장된 전체 QA 개수

num_samples = 20    # 셈플로 추출할 QA 개수

# (qeustion, answer) 쌍을 리스트로 변환 후 앞 20개만 자르고, 다시 dict로 재구성
final_refined_dict = dict(list(refined_dict.items())[:num_samples])
final_refined_dict

5764


{'임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?': '1989년 2월 15일',
 '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?': '임수경',
 '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?': '1989년',
 '임종석을 검거한 장소는 경희대 내 어디인가?': '학생회관 건물 계단',
 '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?': '서울지방경찰청 공안분실',
 '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?': '임종석',
 '임종석이 1989년 2월 15일에 지명수배 받은 혐의는 어떤 시위를 주도했다는 것인가?': '여의도 농민 폭력 시위',
 '정부의 헌법개정안 준비 과정에 대해서 청와대 비서실이 아니라 국무회의 중심으로 이뤄졌어야 했다고 지적한 원로 헌법학자는?': '허영',
 "'행보가 비서 본연의 역할을 벗어난다', '장관들과 내각이 소외되고 대통령비서실의 권한이 너무 크다'는 의견이 제기된 대표적인 예는?": '10차 개헌안 발표',
 '국무회의의 심의를 거쳐야 한다는 헌법 제 몇 조의 내용인가?': '제89조',
 '법무부 장관을 제쳐놓고 민정수석이 개정안을 설명하는 게 이해가 안 된다고 지적한 경희대 석좌교수 이름은?': '허영',
 '미국 군대 내 두번째로 높은 직위는 무엇인가?': '미국 육군 부참모 총장',
 '로널드 레이건 정부 출범 당시 알렉산더 헤이그는 어떤 직책을 맡았는가?': '초대 국무장관직',
 '알렉산더 헤이그는 어느 대통령의 밑에서 국무장관을 지냈는가?': '로널드 레이건 대통령',
 '로널드 레이건 대통령 밑에서 일한 국무 장관은 누구인가?': '알렉산더 메이그스 헤이그 2세',
 '미국 군대에서 두번째로 높은 직위는?': '미국 육군 부참모 총장',
 '알렉산더 메이그스 헤이그의 생년월일은?': '1924년 12월 2일',
 '알렉산더 헤이그가 로널드 레이건 대통령 밑에서 맡은 직책은 무엇이었나?': '국무장

In [7]:
results = []            # 변환된 학습 샘플을 담은 리스트

for q, a in final_refined_dict.items(): # (질문 q, 답변 a) 쌍을 순회
    messages = {
        'messages':[
            {'role':'system','content':'당신은 정보력이 강한 챗봇입니다.'},  # 시스템 프롬프트
            {'role':'user','content':q},                                    # 유저 프름포트 (질문)
            {'role':'assistant','content':a},                               # 정답(모델에 학습할 목표 응답)
        ]
    }
    results.append(messages)
    
print(len(results))
results # 변환된 messages 구조

20


[{'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?'},
   {'role': 'assistant', 'content': '1989년 2월 15일'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?'},
   {'role': 'assistant', 'content': '임수경'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?'},
   {'role': 'assistant', 'content': '1989년'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석을 검거한 장소는 경희대 내 어디인가?'},
   {'role': 'assistant', 'content': '학생회관 건물 계단'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?'},
   {'role': 'assistant', 'content': '서울지방경찰청 공안분실'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},


In [8]:
# UTF-8로 JSONL 파일 생성/열기 (한글 보존)
with open('korquad_finetuning_train.jsonl','w',encoding='utf-8') as f:
    for qa in results:  # 변환된 학습 샘플들을 순회
        # 샘플로 JSON 문자열로 변환 후 한 줄씩 기록(JSONL 포맷)
        f.write(json.dumps(qa,ensure_ascii=False)+'\n')

## 파인튜닝

# 평가
학습한 20개 데이터에 대해 아래 항목을 포함한 json파일을 생성
- question
- answer

In [9]:
val_results = []    # 검증데이터(질문/정답 쌍)을 담은 리스트

for q,a in final_refined_dict.items():  #(질문,정답)쌍을 순회
    data = {
        'messages':[
            {'role': 'system', 'content': "당신은 정보력이 강한 챗봇입니다."},
            {'role':'user' ,'content': q},      # 유저프롬프트(질문)
            {'role':'assistant','content': a}    # 정답(모델이 학습할 목표 응답)
        ]
    }
    val_results.append(data)    # 생성한 샘플을 리스트에 추가
    
print(len(val_results)) # 생성된 검증 샘플 개수
val_results     # 검증 데이터 리스트

20


[{'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?'},
   {'role': 'assistant', 'content': '1989년 2월 15일'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?'},
   {'role': 'assistant', 'content': '임수경'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?'},
   {'role': 'assistant', 'content': '1989년'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석을 검거한 장소는 경희대 내 어디인가?'},
   {'role': 'assistant', 'content': '학생회관 건물 계단'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},
   {'role': 'user', 'content': '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?'},
   {'role': 'assistant', 'content': '서울지방경찰청 공안분실'}]},
 {'messages': [{'role': 'system', 'content': '당신은 정보력이 강한 챗봇입니다.'},


In [10]:
import os       # 파일 경로/존재 확인용
import json     # dict -> JSON 문자열로 변환용

output_path = 'korquad_finetuning_validation.jsonl'     # 저장할 팔일명
with open(output_path,'w',encoding='utf-8') as f:       # UTF-8로 파일 쓰기모드 열기
    for qa in val_results:  # 검증 데이터 순회
        f.write(json.dumps(qa,ensure_ascii=False)+ '\n')    # JSON 객체 1개를 한 줄(JSONL)로 저장
        
print("저장 완료", os.path.abspath(output_path))        # 파일의 절대경로
print("파일 존재 여부",os.path.exists(output_path))     # 파일 생성여부

저장 완료 c:\Users\Playdata\llm\04_gpt_finetuning\korquad_finetuning_validation.jsonl
파일 존재 여부 True


In [11]:
from openai import OpenAI                 # OpenAI API를 사용하기 위한 클라이언트 클래스
from dotenv import load_dotenv
import os

load_dotenv()
os.environ["OPENAI_API_KEY"] = os.getenv('openai_key')
OPENWEATHER_API_KEY = os.getenv('openweather_key')
OPENWEATHER_API_KEY

'c9c41a782930cfc8c78bdeb5584b16b0'

In [12]:
client=OpenAI()

FINE_TUNED_MODEL = 'ft:g'
SYSTEM = "당신은 정보력이 강한 챗봇입니다."

# fine_tuned 모델에 질문을 보내고 답변 텍스트만 반환하는 함수
def run_ft_chat(user_text:str):
    response = client.chat.completions.create(
        model='gpt-4.1-mini-2025-04-14',
        messages=[
            {"role" : "system", 'content' : SYSTEM} ,
            {"role" : "user", 'content' : user_text},
        ],
        response_format={"type":"text"},
        temperature=1,
        top_p=1,
        max_completion_tokens=2048,
        frequency_penalty=0,
        presence_penalty=0,
        store=False
    )
    return response.choices[0].message.content

In [13]:
run_ft_chat('1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?')

'1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은 김영수입니다.'